In [55]:
import pandas as pd
import numpy as np
import tensorflow as tf
import os
from os import listdir
from os.path import isfile, join
from collections import namedtuple
from tensorflow.python.layers.core import Dense
from tensorflow.python.ops.rnn_cell_impl import _zero_state_tensors
import time
import re
from sklearn.model_selection import train_test_split
import difflib
import json

In [56]:
def load_book(path):
    """Load a book from its file"""
    input_file = os.path.join(path)
    with open(input_file) as f:
        book = f.read()
    return book

In [57]:
path = './books/'
book_files = [f for f in listdir(path) if isfile(join(path, f))]
book_files = book_files[1:]

books = [] # books data ka array
for book in book_files:
    books.append(load_book(path+book))

In [58]:
books[0]

'{\\rtf1\\ansi\\ansicpg1252\\cocoartf1404\\cocoasubrtf470\n{\\fonttbl\\f0\\fmodern\\fcharset0 Courier;}\n{\\colortbl;\\red255\\green255\\blue255;\\red0\\green0\\blue0;}\n\\margl1440\\margr1440\\vieww10800\\viewh8400\\viewkind0\n\\deftab720\n\\pard\\pardeftab720\\sl280\\partightenfactor0\n\n\\f0\\fs24 \\cf2 \\expnd0\\expndtw0\\kerning0\n\\outl0\\strokewidth0 \\strokec2       The Project Gutenberg EBook of Anna Karenina, by Leo Tolstoy\\\n\\\n\\\nThis eBook is for the use of anyone anywhere at no cost and with almost\\\nno restrictions whatsoever. You may copy it, give it away or re-use it\\\nunder the terms of the Project Gutenberg License included with this\\\neBook or online at http://www.gutenberg.org/license.\\\n\\\n\\\n\\\nTitle: Anna Karenina\\\nAuthor: Leo Tolstoy\\\nRelease Date: July 01, 1998 [EBook #1399]\\\nReposted: April 02, 2005 [corrections, reposted to new folder structure\\\nby David Widger]\\\nReposted: December 09, 2011 [corrections]\\\nReposted: December 15, 2012 [co

In [59]:
def clean_text(text):
    #Remove unwanted characters and extra spaces from the text
    text = re.sub(r'\n', ' ', text) 
    text = re.sub(r'[{}@_*>()\\#%+=\[\]]','', text)
    text = re.sub('a0','', text)
    text = re.sub('\'92t','\'t', text)
    text = re.sub('\'92s','\'s', text)
    text = re.sub('\'92m','\'m', text)
    text = re.sub('\'92ll','\'ll', text)
    text = re.sub('\'91','', text)
    text = re.sub('\'92','', text)
    text = re.sub('\'93','', text)
    text = re.sub('\'94','', text)
    text = re.sub('\.','. ', text)
    text = re.sub('\!','', text)
    text = re.sub('\?','', text)
    text = re.sub(' +',' ', text)
    text = re.sub(',','', text)
    text = re.sub('-','', text)
    text = re.sub('; ','', text)
    text = re.sub(':','', text)
    text = re.sub('"','', text)
    text = re.sub("'97",'\'', text)
    return text

In [60]:
# Clean the text of the books
clean_books = []
for book in books:
    book.lower()
    clean_books.append(clean_text(book))
print(clean_books[0]) 

rtf1ansiansicpg1252cocoartf1404cocoasubrtf470 fonttblf0fmodernfcharset0 Couriercolortbl;red255green255blue255;red0green0blue0margl1440margr1440vieww10800viewh8400viewkind0 deftab720 pardpardeftab720sl280partightenfactor0 f0fs24 cf2 expnd0expndtw0kerning0 outl0strokewidth0 strokec2 The Project Gutenberg EBook of Anna Karenina by Leo Tolstoy This eBook is for the use of anyone anywhere at no cost and with almost no restrictions whatsoever. You may copy it give it away or reuse it under the terms of the Project Gutenberg License included with this eBook or online at http//www. gutenberg. org/license. Title Anna Karenina Author Leo Tolstoy Release Date July 01 1998 EBook 1399 Reposted April 02 2005 corrections reposted to new folder structure by David Widger Reposted December 09 2011 corrections Reposted December 15 2012 corrections conversion to HTML Reposted February 14 2013 conversion to XHTML Strict by David Widger Reposted February 22 2013 corrections conversion to RST by Andrew Sly L

In [61]:
'''file_object = open("clean_books.txt", "w")
for book in clean_books:
  file_object.write("%s. " % book)

file_object.close()'''

'file_object = open("clean_books.txt", "w")\nfor book in clean_books:\n  file_object.write("%s. " % book)\n\nfile_object.close()'

In [62]:
# Create a dictionary to convert the vocabulary (characters) to integers
vocab_to_int = {}
'''count = 0
for book in clean_books:
    for character in book:
        if character not in vocab_to_int:
            vocab_to_int[character] = count
            count += 1'''
with open("./clean_data/vocab_to_int.json", 'r') as f:
        vocab_to_int = json.load(f)
count = len(vocab_to_int)

In [63]:
# Add special tokens to vocab_to_int
'''codes = ['<PAD>','<EOS>','<GO>']
for code in codes:
    vocab_to_int[code] = count
    count += 1'''

"codes = ['<PAD>','<EOS>','<GO>']\nfor code in codes:\n    vocab_to_int[code] = count\n    count += 1"

In [64]:
# Create another dictionary to convert integers to their respective characters
int_to_vocab = {}
for character, value in vocab_to_int.items():
    int_to_vocab[value] = character

In [65]:
'''import json
json = json.dumps(vocab_to_int)
f = open("vocab_to_int.json","w")
f.write(json)
f.close()'''

'import json\njson = json.dumps(vocab_to_int)\nf = open("vocab_to_int.json","w")\nf.write(json)\nf.close()'

In [66]:
'''print(type(int_to_vocab))
import json
json = json.dumps(int_to_vocab)
f = open("int_to_vocab.json","w")
f.write(json)
f.close()'''

'print(type(int_to_vocab))\nimport json\njson = json.dumps(int_to_vocab)\nf = open("int_to_vocab.json","w")\nf.write(json)\nf.close()'

In [67]:
# Split the text from the books into sentences.
sentences = []
'''for book in clean_books:
    for sentence in book.split('. '):
        sentences.append("%s. " % sentence.lower())'''
text_file = open("./clean_data/sentences.txt",'r')
sentences = text_file.read().split(". ")

In [68]:
'''file_object = open("sentences.txt", "w")
for sentence in sentences:
  file_object.write("%s" % sentence)

file_object.close()'''

'file_object = open("sentences.txt", "w")\nfor sentence in sentences:\n  file_object.write("%s" % sentence)\n\nfile_object.close()'

In [69]:
words_list = {}
for i in range(0,len(sentences)):
  temp_list = sentences[i].split(" ")
  for j in range(0,len(temp_list)):
    if temp_list[j] in words_list:
      val = words_list[temp_list[j]]
      val = val+1
      words_list[temp_list[j]] = val
    else:
      words_list[temp_list[j]] = 1

In [70]:
# Convert sentences to integers
int_sentences = []

for sentence in sentences:
    int_sentence = []
    for character in sentence:
        if character != "\n":
            int_sentence.append(vocab_to_int[character])
    int_sentences.append(int_sentence)



In [71]:
print(int_sentences[0])

[0, 1, 2, 3, 4, 5, 6, 7, 4, 5, 6, 7, 8, 9, 10, 3, 11, 12, 11, 8, 13, 8, 13, 4, 0, 1, 2, 3, 14, 15, 14, 8, 13, 8, 13, 4, 6, 16, 17, 0, 1, 2, 14, 18, 15, 19, 2, 13, 5, 1, 1, 17, 20, 2, 15, 2, 21, 13, 22, 23, 0, 5, 2, 8, 24, 4, 0, 6, 23, 1, 15, 19, 8, 13, 16, 0, 7, 23, 0, 8, 13, 20, 13, 0, 1, 17, 20, 26, 0, 23, 22, 11, 12, 12, 10, 0, 23, 23, 5, 11, 12, 12, 17, 20, 16, 23, 11, 12, 12, 26, 0, 23, 22, 15, 10, 0, 23, 23, 5, 15, 17, 20, 16, 23, 15, 21, 4, 0, 10, 20, 3, 14, 14, 15, 21, 4, 0, 10, 0, 3, 14, 14, 15, 27, 7, 23, 28, 28, 3, 15, 29, 15, 15, 27, 7, 23, 28, 24, 29, 14, 15, 15, 27, 7, 23, 28, 30, 7, 5, 22, 15, 19, 22, 23, 2, 1, 4, 17, 18, 11, 15, 19, 9, 4, 0, 22, 9, 4, 0, 22, 23, 2, 1, 4, 17, 18, 11, 15, 6, 20, 11, 29, 15, 9, 4, 0, 1, 7, 10, 24, 1, 23, 5, 2, 4, 8, 1, 13, 0, 15, 19, 2, 15, 2, 6, 11, 14, 19, 8, 2, 11, 19, 23, 31, 9, 5, 22, 15, 23, 31, 9, 5, 22, 1, 28, 15, 30, 23, 0, 5, 7, 5, 10, 15, 19, 13, 16, 1, 20, 15, 6, 1, 0, 13, 30, 23, 28, 7, 22, 1, 24, 15, 19, 6, 1, 0, 13, 30, 23, 

In [72]:
# Find the length of each sentence
lengths = []
for sentence in int_sentences:
    lengths.append(len(sentence))
lengths = pd.DataFrame(lengths, columns=["counts"])

In [73]:
lengths.describe()

counts
count  142981.000000
mean      122.857722
std       224.772691
min         0.000000
25%        44.000000
50%        90.000000
75%       160.000000
max     29544.000000

In [74]:
max_length = 92
min_length = 10

In [75]:
good_sentences = []

for sentence in int_sentences:
    if len(sentence) <= max_length and len(sentence) >= min_length:
        good_sentences.append(sentence)

In [76]:
print("We will use {} to train and test our model.".format(len(good_sentences)))

We will use 63778 to train and test our model.


In [77]:
# Split the data into training and testing sentences
training, testing = train_test_split(good_sentences, test_size = 0.15, random_state = 2)

print("Number of training sentences:", len(training))
print("Number of testing sentences:", len(testing))

Number of training sentences: 54211
Number of testing sentences: 9567


In [78]:
# Sort the sentences by length to reduce padding, which will allow the model to train faster
training_sorted = []
testing_sorted = []

for i in range(min_length, max_length+1):
    for sentence in training:
        if len(sentence) == i:
            training_sorted.append(sentence)
    for sentence in testing:
        if len(sentence) == i:
            testing_sorted.append(sentence)

In [79]:
#used to modify sentences and create noise
letters = ['a','b','c','d','e','f','g','h','i','j','k','l','m',
           'n','o','p','q','r','s','t','u','v','w','x','y','z',]

In [80]:
def noise_maker(sentence, threshold):
    '''Relocate, remove, or add characters to create spelling mistakes'''
    
    noisy_sentence = []
    i = 0
    while i < len(sentence):
        random = np.random.uniform(0,1,1)
        # Most characters will be correct since the threshold value is high
        if random < threshold:
            noisy_sentence.append(sentence[i])
        else:
            new_random = np.random.uniform(0,1,1)
            # ~33% chance characters will swap locations
            if new_random > 0.67:
                if i == (len(sentence) - 1):
                    # If last character in sentence, it will not be typed
                    continue
                else:
                    # if any other character, swap order with following character
                    noisy_sentence.append(sentence[i+1])
                    noisy_sentence.append(sentence[i])
                    i += 1
            # ~33% chance an extra lower case letter will be added to the sentence
            elif new_random < 0.33:
                random_letter = np.random.choice(letters, 1)[0]
                noisy_sentence.append(vocab_to_int[random_letter])
                noisy_sentence.append(sentence[i])
            # ~33% chance a character will not be typed
            else:
                pass     
        i += 1
    return noisy_sentence

In [81]:
def model_inputs():
  
    tf.device("/device:GPU:0")
    '''Create palceholders for inputs to the model'''
    
    with tf.name_scope('inputs'):
        inputs = tf.placeholder(tf.int32, [None, None], name='inputs')
    with tf.name_scope('targets'):
        targets = tf.placeholder(tf.int32, [None, None], name='targets')
    keep_prob = tf.placeholder(tf.float32, name='keep_prob')
    inputs_length = tf.placeholder(tf.int32, (None,), name='inputs_length')
    targets_length = tf.placeholder(tf.int32, (None,), name='targets_length')
    #targets_length = tf.Variable([2, 3, 5, 7, 11], tf.int32)
    max_target_length = tf.reduce_max(targets_length, name='max_target_len')
    #max_target_length = tf.to_int32(max_target_len, name='ToInt32')
    #max_target_length =

    
    #print("max_length:", tf.Print(max_target_length,[max_target_length]))
   

    return inputs, targets, keep_prob, inputs_length, targets_length ,max_target_length  #tf.reduce_max(targets_length,name='max_target_len')

In [82]:
def process_encoding_input(targets, vocab_to_int, batch_size):
    '''Remove the last word id from each batch and concat the <GO> to the begining of each batch'''
    
    with tf.name_scope("process_encoding"):
        ending = tf.strided_slice(targets, [0, 0], [batch_size, -1], [1, 1])
        dec_input = tf.concat([tf.fill([batch_size, 1], vocab_to_int['<GO>']), ending], 1)

    return dec_input

In [83]:
def encoding_layer(rnn_size, sequence_length, num_layers, rnn_inputs, keep_prob, direction):
    '''Create the encoding layer'''
    
    if direction == 1:
        with tf.name_scope("RNN_Encoder_Cell_1D"):
            for layer in range(num_layers):
                with tf.variable_scope('encoder_{}'.format(layer)):
                    lstm = tf.contrib.rnn.LSTMCell(rnn_size)

                    drop = tf.contrib.rnn.DropoutWrapper(lstm, 
                                                         input_keep_prob = keep_prob)

                    enc_output, enc_state = tf.nn.dynamic_rnn(drop, 
                                                              rnn_inputs,
                                                              sequence_length,
                                                              dtype=tf.float32)

            return enc_output, enc_state
        
        
    if direction == 2:
        with tf.name_scope("RNN_Encoder_Cell_2D"):
            for layer in range(num_layers):
                with tf.variable_scope('encoder_{}'.format(layer)):
                    cell_fw = tf.contrib.rnn.LSTMCell(rnn_size)
                    cell_fw = tf.contrib.rnn.DropoutWrapper(cell_fw, 
                                                            input_keep_prob = keep_prob)

                    cell_bw = tf.contrib.rnn.LSTMCell(rnn_size)
                    cell_bw = tf.contrib.rnn.DropoutWrapper(cell_bw, 
                                                            input_keep_prob = keep_prob)

                    enc_output, enc_state = tf.nn.bidirectional_dynamic_rnn(cell_fw, 
                                                                            cell_bw, 
                                                                            rnn_inputs,
                                                                            sequence_length,
                                                                            dtype=tf.float32)
            # Join outputs since we are using a bidirectional RNN
            enc_output = tf.concat(enc_output,2)
            # Use only the forward state because the model can't use both states at once
            return enc_output, enc_state[0]

In [84]:
def training_decoding_layer(dec_embed_input, targets_length, dec_cell, initial_state, output_layer, 
                            vocab_size):
    '''Create the training logits'''
    
    with tf.name_scope("Training_Decoder"):
        training_helper = tf.contrib.seq2seq.TrainingHelper(inputs=dec_embed_input,
                                                            sequence_length=targets_length,
                                                            time_major=False)

        training_decoder = tf.contrib.seq2seq.BasicDecoder(dec_cell,
                                                           training_helper,
                                                           initial_state,
                                                           output_layer) 
        
        #initial_state = dec_cell.zero_state(dtype=tf.float32, batch_size=batch_size)

        training_logits, one,two = tf.contrib.seq2seq.dynamic_decode(training_decoder,
                                                                     output_time_major=False,
                                                                     impute_finished=True,
                                                                     maximum_iterations=tf.reduce_max(targets_length))
        return training_logits

In [85]:
def inference_decoding_layer(embeddings, start_token, end_token, dec_cell, initial_state, output_layer,max_target_length,
                             batch_size,targets_length):
    '''Create the inference logits'''
    
    with tf.name_scope("Inference_Decoder"):
        start_tokens = tf.tile(tf.constant([start_token], dtype=tf.int32), [batch_size], name='start_tokens')

        inference_helper = tf.contrib.seq2seq.GreedyEmbeddingHelper(embeddings,
                                                                    start_tokens,
                                                                    end_token)

        inference_decoder = tf.contrib.seq2seq.BasicDecoder(dec_cell,
                                                            inference_helper,
                                                            initial_state,
                                                            output_layer)

        inference_logits, one_in,two_in = tf.contrib.seq2seq.dynamic_decode(inference_decoder,
                                                                            output_time_major=False,
                                                                            impute_finished=True,
                                                                            maximum_iterations=tf.reduce_max(targets_length))

        return inference_logits

In [86]:
def decoding_layer(dec_embed_input, embeddings, enc_output, enc_state, vocab_size, inputs_length, targets_length, max_target_length,
                   rnn_size, vocab_to_int, keep_prob, batch_size, num_layers,direction):
    '''Create the decoding cell and attention for the training and inference decoding layers'''
    
    with tf.name_scope("RNN_Decoder_Cell"):
        for layer in range(num_layers):
            with tf.variable_scope('decoder_{}'.format(layer)):
                lstm = tf.contrib.rnn.LSTMCell(rnn_size)
                dec_cell = tf.contrib.rnn.DropoutWrapper(lstm, 
                                                         input_keep_prob = keep_prob)
    
    output_layer = Dense(vocab_size,
                         kernel_initializer = tf.truncated_normal_initializer(mean = 0.0, stddev=0.1))
    
    attn_mech = tf.contrib.seq2seq.BahdanauAttention(rnn_size,
                                                  enc_output,
                                                  inputs_length,
                                                  normalize=False,
                                                  name='BahdanauAttention')
    
    with tf.name_scope("Attention_Wrapper"):
        dec_cell = tf.contrib.seq2seq.AttentionWrapper(dec_cell,
                                                              attn_mech,
                                                              rnn_size)
    
    #initial_state = tf.contrib.seq2seq.AttentionWrapperState(enc_state,_zero_state_tensors(rnn_size, batch_size, tf.float32))
    
    #initial_state = dec_cell.zero_state(dtype=tf.float32, batch_size=batch_size)
    
#     attn_zero = dec_cell.zero_state(batch_size , tf.float32 )

#     attn_zero = attn_zero.clone(cell_state = enc_state)
                                                                                        
#     initial_state = tf.contrib.seq2seq.AttentionWrapperState(cell_state = enc_state, 
#                                                               attention = attn_zero,
#                                                               time = 0,
#                                                               alignments=attn_mech,
#                                                               alignment_history=None,
#                                                               attention_state = dec_cell)

#     #initial_state = enc_state
  
    initial_state = dec_cell.zero_state(dtype=tf.float32, batch_size=batch_size).clone(cell_state=enc_state)

    with tf.variable_scope("decode"):
        training_logits = training_decoding_layer(dec_embed_input, 
                                                  targets_length, 
                                                  dec_cell, 
                                                  initial_state,
                                                  output_layer,
                                                  vocab_size)
    with tf.variable_scope("decode", reuse=True):
        inference_logits = inference_decoding_layer(embeddings,  
                                                    vocab_to_int['<GO>'], 
                                                    vocab_to_int['<EOS>'],
                                                    dec_cell, 
                                                    initial_state, 
                                                    output_layer,
                                                    max_target_length,
                                                    batch_size,
                                                   targets_length)

    return training_logits, inference_logits


In [87]:
def seq2seq_model(inputs, targets, keep_prob, inputs_length, targets_length,max_target_length, 
                  vocab_size, rnn_size, num_layers, vocab_to_int, batch_size, embedding_size,direction):
    '''Use the previous functions to create the training and inference logits'''
    
    enc_embeddings = tf.Variable(tf.random_uniform(shape=[vocab_size, embedding_size], minval = -1, maxval = 1, seed = 0.5))
    enc_embed_input = tf.nn.embedding_lookup(enc_embeddings, inputs)
    enc_output, enc_state = encoding_layer(rnn_size, inputs_length, num_layers, 
                                           enc_embed_input, keep_prob,direction)
    
    dec_embeddings = tf.Variable(tf.random_uniform(shape=[vocab_size, embedding_size],minval=-1,maxval= 1,seed = 0.5))
    dec_input = process_encoding_input(targets, vocab_to_int, batch_size)
    dec_embed_input = tf.nn.embedding_lookup(dec_embeddings, dec_input)
    
    training_logits, inference_logits  = decoding_layer(dec_embed_input, 
                                                        dec_embeddings,
                                                        enc_output,
                                                        enc_state, 
                                                        vocab_size, 
                                                        inputs_length, 
                                                        targets_length, 
                                                        max_target_length,
                                                        rnn_size, 
                                                        vocab_to_int, 
                                                        keep_prob, 
                                                        batch_size,
                                                        num_layers,
                                                        direction)
    
    return training_logits, inference_logits


In [88]:
def pad_sentence_batch(sentence_batch):
    """Pad sentences with <PAD> so that each sentence of a batch has the same length"""
    max_sentence = max([len(sentence) for sentence in sentence_batch])
    return [sentence + [vocab_to_int['<PAD>']] * (max_sentence - len(sentence)) for sentence in sentence_batch]


In [89]:
def get_batches(sentences, batch_size, threshold):
    """Batch sentences, noisy sentences, and the lengths of their sentences together.
       With each epoch, sentences will receive new mistakes"""
    
    for batch_i in range(0, len(sentences)//batch_size):
        start_i = batch_i * batch_size
        sentences_batch = sentences[start_i:start_i + batch_size]
        
        sentences_batch_noisy = []
        for sentence in sentences_batch:
            sentences_batch_noisy.append(noise_maker(sentence, threshold))
            
        sentences_batch_eos = []
        for sentence in sentences_batch:
            sentence.append(vocab_to_int['<EOS>'])
            sentences_batch_eos.append(sentence)
            
        pad_sentences_batch = np.array(pad_sentence_batch(sentences_batch_eos))
        pad_sentences_noisy_batch = np.array(pad_sentence_batch(sentences_batch_noisy))
        
        # Need the lengths for the _lengths parameters
        pad_sentences_lengths = []
        for sentence in pad_sentences_batch:
            pad_sentences_lengths.append(len(sentence))
        
        pad_sentences_noisy_lengths = []
        for sentence in pad_sentences_noisy_batch:
            pad_sentences_noisy_lengths.append(len(sentence))
        
        yield pad_sentences_noisy_batch, pad_sentences_batch, pad_sentences_noisy_lengths, pad_sentences_lengths


In [90]:
# The default parameters
epochs = 100
batch_size = 128
num_layers = 3 
rnn_size = 512
embedding_size = 128
learning_rate = 0.007
direction = 2
threshold = 0.75
keep_probability = 0.75

In [91]:
def build_graph(keep_prob, rnn_size, num_layers, batch_size, learning_rate, embedding_size,direction):

    tf.reset_default_graph()
    
    # Load the model inputs    
    inputs, targets, keep_prob, inputs_length, targets_length, max_target_length = model_inputs()

    # Create the training and inference logits
    training_logits, inference_logits = seq2seq_model(tf.reverse(inputs, [-1]),
                                                      targets, 
                                                      keep_prob,   
                                                      inputs_length,
                                                      targets_length,
                                                      max_target_length,
                                                      len(vocab_to_int)+1,
                                                      rnn_size, 
                                                      num_layers, 
                                                      vocab_to_int,
                                                      batch_size,
                                                      embedding_size,
                                                      direction)

    # Create tensors for the training logits and inference logits
    training_logits = tf.identity(training_logits.rnn_output, 'logits')

    with tf.name_scope('predictions'):
        predictions = tf.identity(inference_logits.sample_id, name='predictions')
        tf.summary.histogram('predictions', predictions)

    # Create the weights for sequence_loss
    masks = tf.sequence_mask(targets_length, dtype=tf.float32, name='masks')
    
    with tf.name_scope("cost"):
        # Loss function
        cost = tf.contrib.seq2seq.sequence_loss(training_logits, 
                                                targets, 
                                                masks)
        tf.summary.scalar('cost', cost)

    with tf.name_scope("optimze"):
        optimizer = tf.train.AdamOptimizer(learning_rate)

        # Gradient Clipping
        gradients = optimizer.compute_gradients(cost)
        capped_gradients = [(tf.clip_by_value(grad, -5., 5.), var) for grad, var in gradients if grad is not None]
        train_op = optimizer.apply_gradients(capped_gradients)

    # Merge all of the summaries
    merged = tf.summary.merge_all()    

    # Export the nodes 
    export_nodes = ['inputs', 'targets', 'keep_prob', 'cost', 'inputs_length', 'targets_length',
                    'predictions', 'merged', 'train_op','optimizer']
    Graph = namedtuple('Graph', export_nodes)
    local_dict = locals()
    graph = Graph(*[local_dict[each] for each in export_nodes])
    
    saver = tf.train.Saver()
    return graph, saver

In [92]:
def train(model, epochs, log_string, saver):
    '''Train the RNN'''
    
    with tf.Session() as sess:
        sess.run(tf.global_variables_initializer())

        # Used to determine when to stop the training early
        testing_loss_summary = []

        # Keep track of which batch iteration is being trained
        iteration = 0
        
        display_step = 30 # The progress of the training will be displayed after every 30 batches
        stop_early = 0 
        stop = 5 # If the batch_loss_testing does not decrease in 3 consecutive checks, stop training
        per_epoch = 3 # Test the model 3 times per epoch
        testing_check = (len(training_sorted)//batch_size//per_epoch)-1

        print()
        print("Training Model: {}".format(log_string))

        train_writer = tf.summary.FileWriter('./logs/1/train/{}'.format(log_string), sess.graph)
        test_writer = tf.summary.FileWriter('./logs/1/test/{}'.format(log_string))

        for epoch_i in range(1, epochs+1): 
            batch_loss = 0
            batch_time = 0
            
            for batch_i, (input_batch, target_batch, input_length, target_length) in enumerate(
                    get_batches(training_sorted, batch_size, threshold)):
                start_time = time.time()

                summary, loss, _ = sess.run([model.merged,
                                             model.cost, 
                                             model.train_op], 
                                             {model.inputs: input_batch,
                                              model.targets: target_batch,
                                              model.inputs_length: input_length,
                                              model.targets_length: target_length,
                                              model.keep_prob: keep_probability})


                batch_loss += loss
                end_time = time.time()
                batch_time += end_time - start_time

                # Record the progress of training
                train_writer.add_summary(summary, iteration)

                iteration += 1

                if batch_i % display_step == 0 and batch_i > 0:
                    print('Epoch {:>3}/{} Batch {:>4}/{} - Loss: {:>6.3f}, Seconds: {:>4.2f}'
                          .format(epoch_i,
                                  epochs, 
                                  batch_i, 
                                  len(training_sorted) // batch_size, 
                                  batch_loss / display_step, 
                                  batch_time))
                    batch_loss = 0
                    batch_time = 0

                #### Testing ####
                if batch_i % testing_check == 0 and batch_i > 0:
                    batch_loss_testing = 0
                    batch_time_testing = 0
                    for batch_i, (input_batch, target_batch, input_length, target_length) in enumerate(
                            get_batches(testing_sorted, batch_size, threshold)):
                        start_time_testing = time.time()
                        summary, loss = sess.run([model.merged,
                                                  model.cost], 
                                                     {model.inputs: input_batch,
                                                      model.targets: target_batch,
                                                      model.inputs_length: input_length,
                                                      model.targets_length: target_length,
                                                      model.keep_prob: 1})

                        batch_loss_testing += loss
                        end_time_testing = time.time()
                        batch_time_testing += end_time_testing - start_time_testing

                        # Record the progress of testing
                        test_writer.add_summary(summary, iteration)

                    n_batches_testing = batch_i + 1
                    print('Testing Loss: {:>6.3f}, Seconds: {:>4.2f}'
                          .format(batch_loss_testing / n_batches_testing, 
                                  batch_time_testing))
                    
                    batch_time_testing = 0

                    # If the batch_loss_testing is at a new minimum, save the model
                    testing_loss_summary.append(batch_loss_testing)
                    if batch_loss_testing <= min(testing_loss_summary):
                        print('New Record!') 
                        stop_early = 0
                        checkpoint = "./{}.ckpt".format(log_string)
                        print(checkpoint)
                        
                        #Savind model at data/dm.ckpt
                        save_path = saver.save(sess, checkpoint)
                        print("Done Saving at ", save_path)
                        print(os.getcwd())

                    else:
                        print("No Improvement.")
                        stop_early += 1
                        if stop_early == stop:
                            break

            if stop_early == stop:
                print("Stopping Training.")
                break


In [ ]:
'''for keep_probability in [0.75]:
    for num_layers in [3]:
        for threshold in [0.75]:
            log_string = 'kp={},nl={},th={}'.format(keep_probability,
                                                    num_layers,
                                                    threshold) 
            model, saver = build_graph(keep_probability, rnn_size, num_layers, batch_size, 
                                learning_rate, 
                                embedding_size,
                                direction)
            train(model, epochs, log_string, saver)'''

In [94]:
def text_to_ints(text):
    '''Prepare the text for the model'''
    
    text = clean_text(text)
    return [vocab_to_int[word] for word in text]

In [95]:
testing_dict = {}

test_sen = []

testing_scr = open("input.txt", "r")
value=""

test_sent = testing_scr.read().split('.')
mod = test_sent[0].split("=");
      

In [96]:
test_sent[0] = mod[1]
for i in range(0,len(test_sent)):
    test_sent[i] = test_sent[i].replace("+"," ")
    value = value + test_sent[i]+"."
#print(testing_dict)
print("***************************************************")
# Create your own sentence or use one from the dataset
filestr = ""
for arr in test_sent:
    text = arr
    text = text.lower()
    text = text_to_ints(text)

    

    checkpoint = "./kp=0.75,nl=3,th=0.75.ckpt"
    tf.reset_default_graph()
    model, saver = build_graph(keep_probability, rnn_size, num_layers, batch_size, learning_rate, embedding_size, direction) 

    with tf.Session() as sess:
        # Load saved model
        #saver = tf.train.Saver()
        saver.restore(sess, './kp=0.75,nl=3,th=0.75.ckpt')

        #Multiply by batch_size to match the model's input parameters
        answer_logits = sess.run(model.predictions, {model.inputs: [text]*batch_size, 
                                                    model.inputs_length: [len(text)]*batch_size,
                                                    model.targets_length: [len(text)+1], 
                                                    model.keep_prob: [1.0]})[0]

    # Remove the padding from the generated sentence
    pad = vocab_to_int["<PAD>"] 

    print('\nText')
    print('  Word Ids:    {}'.format([i for i in text]))
    print('  Input Words: {}'.format("".join([int_to_vocab[i] for i in text])))

    pred = ""

    print('\nSummary')
    print('  Word Ids:       {}'.format([i for i in answer_logits if i != pad]))
    print('  Response Words: {}'.format("".join([int_to_vocab[i] for i in answer_logits if i != pad])))
    pred = "".join([int_to_vocab[i] for i in answer_logits if i != pad])
    filestr = filestr+pred+".\n"
    
file = open("mod_input.txt",'w+')
file.write(value)
file.close()

file=open("output.txt",'w+');
file.write(filestr)
file.close()    

***************************************************
INFO:tensorflow:Restoring parameters from ./kp=0.75,nl=3,th=0.75.ckpt

Text
  Word Ids:    [1, 24, 6, 7, 19, 7, 6, 19, 27, 23, 0, 38, 19, 7, 21, 9, 0, 23, 6, 6, 7, 27]
  Input Words: thsi is very impressiv

Summary
  Word Ids:       [1, 24, 7, 6, 19, 7, 6, 19, 27, 23, 0, 38, 19, 7, 21, 9, 0, 23, 6, 6, 7, 27, 23]
  Response Words: this is very impressive
